# Fetching and processing the data


I used [bedtools](http://bedtools.readthedocs.io/en/latest/) to intersect constrained coding regions (CCRs), defined by exonic regions lying between consecutive non-synonymous [gnomAD](http://gnomad.broadinstitute.org/) variants, with somatic mutations observed in cancer genomes ([COSMIC](https://cancer.sanger.ac.uk/cosmic/download)). The result of this analysis is a `pickle` file containing the total multi-exonic length,  number of somatic mutations, and other "features" (e.g. CpG density and synonymous variant density) for each CCR:

In [1]:
import pandas as pd
data_df = pd.read_pickle('ccrs.v2.20180420.lengths_numberMutations.pkl')
data_df = data_df.sample(frac=0.01, random_state=0)

data_df.head()

unique_key  total_number_of_mutations  total_length  chrom  \
1250370     1250371                          1             6      1   
3662076     3662078                          0             4     19   
216081       216082                          1            18      4   
200877       200878                          2            18     11   
3125117     3125118                          0             1     10   

           ccr_pct            gene               ranges   varflag  \
1250370  30.131443            PER3      7854050-7854056  VARFALSE   
3662076   0.033837  CTD-3214H19.16      7747293-7747297  VARFALSE   
216081   75.382350           CASP3  185553031-185553049  VARFALSE   
200877   76.530214           TENM4    78413057-78413075  VARFALSE   
3125117   2.479659          DHTKD1    12139770-12139771  VARFALSE   

         syn_density  cpg  cov_score  resid  resid_pctile  
1250370        0.167  0.0       6.00 -0.043      4.185563  
3662076        0.000  1.0       3.19 -1.765      0.639091  
216081         0.056  0.0      17.82  1.627      7.623689  
200877         0.000  0.0      18.00  1.653      7.676046  
3125117        0.000  0.0       1.00 -0.749      2.731195

# Edit the python path 

Make the modules containing the modeling code visible to this Notebook:


In [2]:
import os 
model_directory = os.path.dirname(os.getcwd()) + '/model'

import sys
sys.path.append(model_directory)

print 'Python searches these paths when asked to import a module:'
for path in sys.path: 
    print(path)

Python searches these paths when asked to import a module:

/anaconda2/envs/tensorflow/lib/python27.zip
/anaconda2/envs/tensorflow/lib/python2.7
/anaconda2/envs/tensorflow/lib/python2.7/plat-darwin
/anaconda2/envs/tensorflow/lib/python2.7/plat-mac
/anaconda2/envs/tensorflow/lib/python2.7/plat-mac/lib-scriptpackages
/anaconda2/envs/tensorflow/lib/python2.7/lib-tk
/anaconda2/envs/tensorflow/lib/python2.7/lib-old
/anaconda2/envs/tensorflow/lib/python2.7/lib-dynload
/anaconda2/envs/tensorflow/lib/python2.7/site-packages
/anaconda2/envs/tensorflow/lib/python2.7/site-packages/IPython/extensions
/Users/petermchale/.ipython
/Users/petermchale/Work/modeling_mutation_counts_using_neural_networks/engineer_features/model


# Modeling

I assume the mutations are Poisson distributed with an average mutation count equal to $lh(x)$ where $l$ is interval length, $x$ is some feature, and a $h$ is a neural network $h(x)$ modeling the unknown mutation rate: 

In [3]:
# train the model using tensorflow and just one feature 
from model import train
data_df_headings = {'l_heading_list': ['total_length'],
                    'X_heading_list': ['syn_density'],
                    'y_heading_list': ['total_number_of_mutations']}
log_df = train(data_df, **data_df_headings)
log_df

Instructions for updating:
Use the retry module or similar alternatives.


epoch      cost  likelihood      bias    weight
0     0.0  5.117680         0.0 -0.100000 -1.154452
1    10.0  1.948738         0.0 -1.021510 -2.051920
2    20.0  1.331807         0.0 -1.664027 -2.583327
3    30.0  1.266611         0.0 -2.008585 -2.731580
4    40.0  1.269745         0.0 -2.143325 -2.616213
5    50.0  1.264065         0.0 -2.160345 -2.352807
6    60.0  1.251779         0.0 -2.127649 -2.023236
7    70.0  1.240969         0.0 -2.088615 -1.680328
8    80.0  1.233528         0.0 -2.065691 -1.354487
9    90.0  1.228032         0.0 -2.064551 -1.058100
10  100.0  1.223312         0.0 -2.080038 -0.790815
11  110.0  1.219202         0.0 -2.103251 -0.546655
12  120.0  1.215763         0.0 -2.126981 -0.320331
13  130.0  1.213015         0.0 -2.147756 -0.110152
14  140.0  1.210866         0.0 -2.165152  0.082431
15  150.0  1.209254         0.0 -2.180089  0.254874
16  160.0  1.208064         0.0 -2.193471  0.405398
17  170.0  1.207243         0.0 -2.205647  0.533809
18  180.0  1.206659         0.0 -2.216519  0.641325
19  190.0  1.206289         0.0 -2.225874  0.729945
20  200.0  1.206052         0.0 -2.233626  0.801901
21  210.0  1.205900         0.0 -2.239867  0.859382
22  220.0  1.205809         0.0 -2.244793  0.904484
23  230.0  1.205760         0.0 -2.248624  0.939217
24  240.0  1.205744         0.0 -2.251557  0.965475
25  250.0  1.205718         0.0 -2.253759  0.984979
26  260.0  1.205716         0.0 -2.255376  0.999219
27  270.0  1.205714         0.0 -2.256537  1.009435
28  280.0  1.205718         0.0 -2.257355  1.016632
29  290.0  1.205712         0.0 -2.257921  1.021603

# Analysis of learned model 

In [5]:
%matplotlib inline 

from plot import plot_counts
plot_counts(data_df, **data_df_headings)

The deviation of observations from expectation indicates that the model is incomplete. 